In [ ]:
# Loading the SVO

import pickle as p

with open('/Datasets/svo_en_large.dat', 'rb') as f:
  (Sub_dict, Verb_dict, Obj_dict, svo_list) = p.load(f)

In [ ]:
# Loading the SVO full BNC

import pickle as p
with open('/Datasets/svo.dat', 'rb') as f:
  (Sub_dict, Verb_dict, Obj_dict, svo_list) = p.load(f)

In [ ]:
sorted( ((v,k) for k,v in d.iteritems()), reverse=True)

('that', "'s", 'it'): 608
('that', "'s", 'one'): 183
('it', "'s", 'one'): 175
('that', "'s", 'all'): 174
('i', "'", 'm'): 139
('there', "'s", 'one'): 133
('i', 'tell', 'you'): 129
('i', 'told', 'you'): 107
('you', 'do', 'it'): 105
('there', "'s", 'nothing'): 105
('there', "'s", 'lot'): 100
('it', "'s", 'it'): 98
('there', 'wa', 'nothing'): 97
('i', "'ll give", 'you'): 83
('i', "'ll tell", 'you'): 79
('there', 'is', 'evidence'): 78
('it', "'s", 'a'): 71
('there', 'wa', 'something'): 70
('he', 'wa', 'man'): 68
('it', "'s", 'time'): 66
('i', 'got', 'it'): 65
('it', 'wa', 'time'): 64
('i', 'know', 'that'): 63
('i', 'got', 'one'): 63
('it', 'wa', 'one'): 61
("'s", 'have', 'look'): 61
('there', "'s", 'something'): 60
('i', 'like', 'it'): 60
('that', "'s", 'way'): 59
('it', "'s", 'something'): 59
('it', "'s gon", 'na be'): 57
('you', 'put', 'it'): 55
('that', "'s", 'thing'): 55
('it', "'s", '’'): 55
('you', 'want', 'to go'): 54
('you', 'know', 'that'): 54
('it', "'s", 'thing'): 53
('there', '

In [ ]:
# Creating the dictionary structure for svo, sv, vo and subject, verb and object

# Notes down the total tokens of each
svo_total = 0
sub_total = 0
verb_total = 0
obj_total = 0
sv_total = 0
vo_total = 0

# Notes down the total types of each
svo_key = len(svo_list.keys())
sub_key = len(Sub_dict.keys())
obj_key = len(Obj_dict.keys())
verb_key = len(Verb_dict.keys())

sv_dict = {}
vo_dict = {}

for i in svo_list:
  svo_total+=svo_list[i]
  try:
    sv_dict[(i[0],i[1])]+=1
  except KeyError:
    sv_dict[(i[0],i[1])]=1
  try:
    vo_dict[(i[1],i[2])]+=1
  except KeyError:
    vo_dict[(i[1],i[2])]=1

for s in Sub_dict:
  sub_total += Sub_dict[s]
for v in Verb_dict:
  verb_total += Verb_dict[v]
for o in Obj_dict:
  obj_total += Obj_dict[o]

sv_key = len(sv_dict.keys())
vo_key = len(vo_dict.keys())

for sv in sv_dict:
  sv_total += sv_dict[sv]
for vo in vo_dict:
  vo_total += vo_dict[vo]

In [ ]:
# Creating a scoring object for easy access

score_obj = {
    'svo':svo_list,
    'sub':Sub_dict,
    'verb':Verb_dict,
    'obj':Obj_dict,
    'sv':sv_dict,
    'vo':vo_dict,
    'token_sv':sv_total,
    'token_vo':vo_total,
    'token_sub':sub_total,
    'token_verb':verb_total,
    'token_obj':obj_total,
    'token_svo':svo_total,
    'type_sub':sub_key,
    'type_verb':verb_key,
    'type_obj':obj_key,
    'type_svo':svo_key,
    'type_sv':sv_key,
    'type_vo':vo_key
}

In [ ]:
score_obj['svo'][('she','play','race')] += 48

In [ ]:
score_obj['token_svo']+=48
score_obj['token_sv']+=48
score_obj['token_vo']+=48
score_obj['token_sub']+=48
score_obj['token_verb']+=48
score_obj['token_obj']+=48

In [ ]:
score_obj['sv'][('she','play')]+=48
score_obj['vo'][('play','race')]+=48
score_obj['sub']['she']+=48
score_obj['verb']['play']+=48
score_obj['obj']['race']+=48

In [ ]:
def get_prob(query ,dictionary, tokens, types):
  if query in dictionary:
    return float(dictionary[query]+1)/(tokens + types)
  else:
    return float(1)/(tokens + types)

def cal_mi(sub,verb,obj, score_obj):
  prob_svo = get_prob((sub,verb,obj), score_obj['svo'], score_obj['token_svo'],score_obj['type_svo'])
  prob_sub = get_prob(sub, score_obj['sub'], score_obj['token_sub'],score_obj['type_sub'])
  prob_obj = get_prob(obj, score_obj['obj'], score_obj['token_obj'],score_obj['type_obj'])
  prob_verb = get_prob(verb, score_obj['verb'], score_obj['token_verb'],score_obj['type_verb'])
  prob_sv = get_prob((sub,verb), score_obj['sv'], score_obj['token_sv'],score_obj['type_sv'])
  prob_vo = get_prob((verb,obj), score_obj['vo'], score_obj['token_vo'],score_obj['type_vo'])
    
  mi_svo = prob_svo/(prob_sub*prob_verb*prob_obj)
  mi_sv = prob_sv/(prob_sub*prob_verb)
  mi_vo = prob_vo/(prob_verb*prob_obj)
  
  return mi_svo/(1+mi_svo), mi_sv/(mi_sv+1), mi_vo/(1+mi_vo)

def give_verb_score(sub, verb, obj, verb_t, score_obj):
  if verb in score_obj['verb'] and verb_t in score_obj['verb']:
    
    score = 0
    s_svo, s_sv, s_vo = cal_mi(sub,verb,obj, score_obj)
    s_svto, s_svt, s_vto = cal_mi(sub,verb_t,obj, score_obj)
    
    score+=(s_svto-s_svo)/(s_svto+s_svo)
    if s_svto > s_svo+0.01*s_svo*(1-s_svo):
      return score
    score+=(s_svt-s_sv)/(s_vto+s_vo)
    score+=(s_svt-s_sv)/(s_vto+s_vo)
    
    return score/3
    
  else:
    return -1


In [ ]:
import nltk

In [ ]:
nltk.download('wordnet')

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.


True

In [ ]:
# Loading NLTK lemmatizer
from nltk.stem import WordNetLemmatizer
lemmatizer = WordNetLemmatizer()

In [ ]:
import pandas as pd

In [ ]:
# Loading Dataset
eval_data_set3 = pd.read_csv('Datasets/TestingDatasets/GS2011data.txt', sep=' ')

In [ ]:
eval_data_set3.head(500)

participant     verb     subject  object landmark  input  hilo
0    participant20  provide      family    home   supply      4  HIGH
1    participant20  provide  government    cash    leave      3   LOW
2    participant20  provide  government    cash   supply      7  HIGH
3    participant20  provide         man   money    leave      6  HIGH
4    participant20  provide         man   money   supply      7  HIGH
..             ...      ...         ...     ...      ...    ...   ...
495  participant24      say      priest  prayer    state      2   LOW
496  participant24      say     speaker    word   allege      1   LOW
497  participant24      say      people  prayer    state      3   LOW
498  participant24      say      priest  prayer   allege      1   LOW
499  participant24      say      priest    mass    state      2   LOW

[500 rows x 7 columns]

In [ ]:
# Calculating model score after lemmatizig test data svovt

model_score = []
for svovt in zip(eval_data_set3['subject'],eval_data_set3['verb'],eval_data_set3['object'],eval_data_set3['landmark']):
  sub = lemmatizer.lemmatize(svovt[0])
  obj = lemmatizer.lemmatize(svovt[2])
  vv = lemmatizer.lemmatize(svovt[1])
  vt = lemmatizer.lemmatize(svovt[3])
  model_score.append(give_verb_score(sub,vv,obj,vt, score_obj))

In [ ]:
# Calculating Spearman correlation and pvalue
from scipy.stats import spearmanr
print(spearmanr(model_score,eval_data_set3['input']))

SpearmanrResult(correlation=0.2596322730416683, pvalue=8.526142545235745e-40)


In [ ]:
score_removed = []
score_removed_model = []
for i in range(len(eval_data_set3['subject'])):
  if model_score[i]!=-1:
    score_removed.append(eval_data_set3['input'][i])
    score_removed_model.append(model_score[i])

In [ ]:
print(spearmanr(score_removed_model,score_removed))

SpearmanrResult(correlation=0.2346801998386863, pvalue=4.2155761789785505e-28)


In [ ]:
# Spearman Correlation for each participant
for i in range(0,2500, 100):
  print("Participant",i//100+1,":",spearmanr(model_score[i:i+100],eval_data_set3['input'][i:i+100]))

Participant 1 : SpearmanrResult(correlation=0.4321558347211653, pvalue=7.1302780798933554e-06)
Participant 2 : SpearmanrResult(correlation=0.43460178520012877, pvalue=6.2420178714248885e-06)
Participant 3 : SpearmanrResult(correlation=0.44639256702969393, pvalue=3.239069362840132e-06)
Participant 4 : SpearmanrResult(correlation=0.327833615653798, pvalue=0.0008695870229531738)
Participant 5 : SpearmanrResult(correlation=0.18169079089340998, pvalue=0.07042699213819671)
Participant 6 : SpearmanrResult(correlation=0.25483684195349804, pvalue=0.01050576219894229)
Participant 7 : SpearmanrResult(correlation=0.35732160573468047, pvalue=0.00026270111290898094)
Participant 8 : SpearmanrResult(correlation=0.17815768027310344, pvalue=0.07616339014534933)
Participant 9 : SpearmanrResult(correlation=0.39021565023728016, pvalue=5.984738650845949e-05)
Participant 10 : SpearmanrResult(correlation=0.18736133653275705, pvalue=0.06195413822699782)
Participant 11 : SpearmanrResult(correlation=0.3171706481

In [ ]:
score_removed = []
score_removed_model = []
for i in range(len(eval_data_set3['subject'])):
  if eval_data_set3['hilo'][i]=="HIGH":
    score_removed.append(eval_data_set3['input'][i])
    score_removed_model.append(model_score[i])

In [ ]:
print(spearmanr(score_removed_model,score_removed))

SpearmanrResult(correlation=0.16671013356097383, pvalue=1.0700542678483895e-08)


In [ ]:
score_removed = []
score_removed_model = []
for i in range(len(eval_data_set3['subject'])):
  if eval_data_set3['hilo'][i]=="LOW":
    score_removed.append(eval_data_set3['input'][i])
    score_removed_model.append(model_score[i])

In [ ]:
print(spearmanr(score_removed_model,score_removed))

SpearmanrResult(correlation=0.17095570090360057, pvalue=3.143722741100925e-10)


In [ ]:
np.unique(eval_data_set3['participant'])

array(['participant1', 'participant10', 'participant11', 'participant12',
       'participant13', 'participant14', 'participant15', 'participant16',
       'participant17', 'participant18', 'participant19', 'participant2',
       'participant20', 'participant21', 'participant22', 'participant23',
       'participant24', 'participant25', 'participant3', 'participant4',
       'participant5', 'participant6', 'participant7', 'participant8',
       'participant9'], dtype=object)

In [ ]:
import numpy as np

In [ ]:
eval_data_set3.tail(100)

participant     verb     subject  object landmark  input  hilo
2400  participant8  provide      family    home   supply      5  HIGH
2401  participant8  provide  government    cash    leave      2   LOW
2402  participant8  provide  government    cash   supply      6  HIGH
2403  participant8  provide         man   money    leave      3  HIGH
2404  participant8  provide         man   money   supply      6  HIGH
...            ...      ...         ...     ...      ...    ...   ...
2495  participant8      say      priest  prayer    state      2   LOW
2496  participant8      say     speaker    word   allege      4   LOW
2497  participant8      say      people  prayer    state      2   LOW
2498  participant8      say      priest  prayer   allege      3   LOW
2499  participant8      say      priest    mass    state      1   LOW

[100 rows x 7 columns]

In [ ]:
binary = []
for i in range(len(eval_data_set3['subject'])):
  if eval_data_set3['hilo'][i]=="HIGH":
    binary.append(1)
  else:
    binary.append(0)

In [ ]:
print(spearmanr(model_score,binary))

SpearmanrResult(correlation=0.2314170739611216, pvalue=9.538291969444396e-32)


In [ ]:
list(zip(binary, model_score))

[(1, 2.1039406069259845e-05),
 (0, -0.025560527839839215),
 (1, 1.9201019934257225e-05),
 (1, 0.013013416360182448),
 (1, 0.00039254075114464744),
 (0, -0.019804291239732316),
 (1, 2.9012155101375017e-05),
 (1, 2.0631598361127384e-06),
 (0, -0.012667191857790867),
 (1, 2.0815736062753947e-05),
 (0, 2.60964568679321e-06),
 (1, 1.727087455783852e-05),
 (1, 2.129742831047698e-06),
 (1, 2.407892676366535e-05),
 (0, 0.00014995906578082216),
 (1, 0.0001071090292806277),
 (1, 3.6535077753192977e-06),
 (1, 2.6443082671439905e-05),
 (0, 8.90040676770413e-07),
 (1, 2.1862539179252808e-05),
 (0, 3.3710822157256596e-05),
 (0, 7.912706039933069e-08),
 (0, 2.894146645978544e-06),
 (0, 1.259328819054726e-06),
 (0, 5.699351933691517e-05),
 (1, 8.905360023043942e-05),
 (0, 3.0607822516857426e-05),
 (0, 3.340801198212364e-05),
 (1, 0.0002054359348049117),
 (1, 0.00028763394486622273),
 (0, 5.233267515872245e-07),
 (1, 7.326576056201897e-07),
 (0, 1.2094646879894678e-06),
 (1, 1.6932513823934785e-06),
 (

In [ ]:
svo_list

{('it', 'seem', 'important'): 2,
 ('answer', 'should have', '’ quality'): 1,
 ('response', 'precede', '’'): 1,
 ('recourse', 'underscore', 'perception'): 1,
 ('they', 'have', 'splendour'): 1,
 ('they', 'have', 'tendency'): 3,
 ('angel', 'is', 'hybrid'): 1,
 ('angel', 'seem', 'to incorporate'): 1,
 ('which', 'hint', 'meaning'): 1,
 ('it', 'lodged', 'to try'): 1,
 ('it', 'lodged', 'answer'): 1,
 ('there', 'wa', 'something'): 70,
 ('i', "did n't make", 'study'): 1,
 ('i', 'followed', 'clue'): 1,
 ('theme', 'wa', 'one'): 1,
 ('it', 'seemed', 'to become'): 1,
 ('they', 'were not', 'transcription'): 1,
 ('they', 'attempted', 'to annihilate'): 1,
 ('they', 'attempted', 'impose'): 1,
 ('they', 'were', 'thing'): 4,
 ('painting', 'seemed', 'to go'): 1,
 ('conquest', 'had', 'impact'): 1,
 ('effort', 'produced', 'disturbance'): 1,
 ('effort', 'produced', 'change'): 1,
 ('spaniard', 'instituted', 'visitas'): 1,
 ('spaniard', 'instituted', 'inspection'): 1,
 ('jesuit', 'brought', 'painter'): 1,
 ('w

In [ ]:
participants = []
testdata = []
fp = open('/Datasets/TestingDatasets/GS2011data.txt', 'r')
line = fp.readline()
line = fp.readline()
while(line):
    a = line.split()
    if(a[0] not in participants):
        participants.append(a[0])
        testdata.append([])
    testdata[-1].append(a)
    line = fp.readline()
fp.close()

In [ ]:
print(model_score[:100])
print(model_score[500:600])


[2.1039406069259845e-05, -0.025560527839839215, 1.9201019934257225e-05, 0.013013416360182448, 0.00039254075114464744, -0.019804291239732316, 2.9012155101375017e-05, 2.0631598361127384e-06, -0.012667191857790867, 2.0815736062753947e-05, 2.60964568679321e-06, 1.727087455783852e-05, 2.129742831047698e-06, 2.407892676366535e-05, 0.00014995906578082216, 0.0001071090292806277, 3.6535077753192977e-06, 2.6443082671439905e-05, 8.90040676770413e-07, 2.1862539179252808e-05, 3.3710822157256596e-05, 7.912706039933069e-08, 2.894146645978544e-06, 1.259328819054726e-06, 5.699351933691517e-05, 8.905360023043942e-05, 3.0607822516857426e-05, 3.340801198212364e-05, 0.0002054359348049117, 0.00028763394486622273, 5.233267515872245e-07, 7.326576056201897e-07, 1.2094646879894678e-06, 1.6932513823934785e-06, 1.494580102083865e-05, 2.0924246521027186e-05, 1.2336278096084227e-05, 2.108963310300189e-05, 1.5239517485888472e-05, 5.611615415954641e-07, 2.1494493171197203e-05, 7.73237413446283e-05, 5.538737253269667e

In [ ]:
# Evaluation

ranks = []
HighScores = []
LowScores = []

for i in range(len(testdata[0])):
    t = model_score[i]
    if (testdata[0][i][6] == 'HIGH'):
        HighScores.append(t)
    else:
        LowScores.append(t)
    summ = 0
    for j in range(len(testdata)):
        summ = summ + int(testdata[j][i][5])
    ranks.append(summ/len(testdata))

In [ ]:
from scipy import spatial
from scipy.stats import spearmanr

In [ ]:
# Spearman correlation coefficient

rho = spearmanr(ranks,model_score[:100])
print(rho)
print("\n")
summ = 0
for i in range(len(HighScores)):
    summ = summ + HighScores[i]
print("High = " + str(summ/len(HighScores)))
print("\n")
summ = 0
for i in range(len(LowScores)):
    summ = summ + LowScores[i]
print("Low = " + str(summ/len(LowScores)))

SpearmanrResult(correlation=0.1412468056147385, pvalue=0.16099045075229143)


High = 0.0003338080329606614


Low = -0.09550416168287762


In [ ]:
fp = open('/Datasets/TestingDatasets/GS2011data.txt', 'r')
line = fp.readline()
line = fp.readline()

groups = {}

while(line):
    a = line.split()
    v = a[1]
    s = a[2]
    o = a[3]
    vt = a[4]
    if (s,o) in groups:
      if (s,v,o, vt) in groups[(s,o)]:
        groups[(s,o)][(s,v,o, vt)]+=int(a[5])
      else:
        groups[(s,o)][(s,v,o, vt)]=int(a[5])
    else:
      groups[(s,o)] = {}
      groups[(s,o)][(s,v,o, vt)]=int(a[5])
    line = fp.readline()
fp.close()

In [ ]:
spearman1 = 0
counter = 0
for so in groups:
  model_score_1 = []
  data_score = []
  for svovt in groups[so]:
    sub = lemmatizer.lemmatize(svovt[0])
    obj = lemmatizer.lemmatize(svovt[2])
    vv = lemmatizer.lemmatize(svovt[1])
    vt = lemmatizer.lemmatize(svovt[3])
    s = give_verb_score(sub,vv,obj,vt, score_obj)
    model_score_1.append(s)
    data_score.append(groups[so][svovt])
  s1 = spearmanr(np.argsort(np.argsort(model_score_1)), data_score)[0]
  if s1 < 2:
    spearman1+=s1
    counter+=1
 
print(spearman1/counter)

0.2783505154639175


/usr/local/lib/python3.6/dist-packages/numpy/lib/function_base.py:2534: RuntimeWarning: invalid value encountered in true_divide
  c /= stddev[:, None]
/usr/local/lib/python3.6/dist-packages/numpy/lib/function_base.py:2535: RuntimeWarning: invalid value encountered in true_divide
  c /= stddev[None, :]
/usr/local/lib/python3.6/dist-packages/scipy/stats/_distn_infrastructure.py:901: RuntimeWarning: invalid value encountered in greater
  return (a < x) & (x < b)
/usr/local/lib/python3.6/dist-packages/scipy/stats/_distn_infrastructure.py:901: RuntimeWarning: invalid value encountered in less
  return (a < x) & (x < b)
/usr/local/lib/python3.6/dist-packages/scipy/stats/_distn_infrastructure.py:1892: RuntimeWarning: invalid value encountered in less_equal
  cond2 = cond0 & (x <= _a)


In [ ]:
import numpy as np

In [ ]:
import pickle as p
with open('Good_english/score_obj_simp','wb') as f:
  p.dump(score_obj, f)

In [ ]:
give_verb_score('she','run','race','sprint', score_obj)

7.812085385303003e-05

In [ ]:
give_verb_score('she','run','race','ply', score_obj)

7.706508528215228e-05

In [ ]:
score_obj['svo'][('i','purchase','idea')]

KeyError: ignored

In [ ]:
give_verb_score('she','run','race','jog', score_obj)

6.53077591312078e-05

In [ ]:
score = []
for v in score_obj['verb']:
  score.append(give_verb_score('she','run','race', v, score_obj))

In [ ]:
[j[1] for j in sorted(list(zip(score,list(score_obj['verb'].keys()))), reverse=True)]

['supervise',
 'felt',
 "'s had",
 "'s got",
 'was wearing',
 "'d had",
 'remembered',
 'had seen',
 'heard',
 'looked',
 'wore',
 'could see',
 'had had',
 'liked',
 'loved',
 'had left',
 'tried',
 "did n't want",
 'had given',
 'noticed',
 'came',
 'watched',
 'handed',
 'was going',
 'pushed',
 'enjoyed',
 'drew',
 'had made',
 'considered',
 'knew',
 'needed',
 'was doing',
 "'s going",
 'kept',
 "did n't know",
 'wanted',
 'feel',
 'wear',
 'had taken',
 "did n't have",
 "'s gon",
 'was trying',
 'passed',
 'saw',
 'raised',
 'started',
 'said',
 'cut',
 'read',
 'must have',
 'went',
 'ran',
 'doe',
 'failed',
 'pulled',
 'held',
 'continued',
 'stopped',
 'picked',
 'caught',
 'would have',
 'shot',
 'met',
 'opened',
 'had told',
 'changed',
 'reached',
 "'d have",
 'found',
 'forced',
 'began',
 'left',
 'set',
 'bought',
 'has had',
 'refused',
 'could get',
 'sent',
 'killed',
 'lost',
 'turned',
 'spent',
 'would like',
 'had',
 'start',
 'wrote',
 'closed',
 'ignored',
 '

In [ ]:
from nltk.corpus import wordnet

In [ ]:
synonyms = []
for syn in wordnet.synsets("run"): 
    for l in syn.lemmas(): 
        synonyms.append(l.name())

In [ ]:
set(synonyms)

{'be_given',
 'black_market',
 'bleed',
 'break_away',
 'bunk',
 'campaign',
 'carry',
 'consort',
 'course',
 'die_hard',
 'discharge',
 'draw',
 'endure',
 'escape',
 'execute',
 'extend',
 'feed',
 'flow',
 'fly_the_coop',
 'foot_race',
 'footrace',
 'function',
 'go',
 'guide',
 'head_for_the_hills',
 'hightail_it',
 'hunt',
 'hunt_down',
 'incline',
 'ladder',
 'lam',
 'lead',
 'lean',
 'melt',
 'melt_down',
 'move',
 'operate',
 'outpouring',
 'pass',
 'persist',
 'play',
 'ply',
 'political_campaign',
 'prevail',
 'race',
 'range',
 'ravel',
 'rill',
 'rivulet',
 'run',
 'run_away',
 'run_for',
 'runnel',
 'running',
 'running_game',
 'running_play',
 'scarper',
 'scat',
 'streak',
 'streamlet',
 'take_to_the_woods',
 'tally',
 'tend',
 'test',
 'track_down',
 'trial',
 'turn_tail',
 'unravel',
 'work'}